In [9]:
# Install GDAL and Geopandas
!apt install gdal-bin python-gdal python3-gdal --quiet
!apt install python3-rtree --quiet
!pip install git+git://github.com/geopandas/geopandas.git --quiet
!pip install descartes --quiet
!pip install geopy
!pip install plotly_express
!pip install ipython-autotime

!pip install tqdm==4.36.0


Reading package lists...
Building dependency tree...
Reading state information...
gdal-bin is already the newest version (2.2.3+dfsg-2).
python-gdal is already the newest version (2.2.3+dfsg-2).
python3-gdal is already the newest version (2.2.3+dfsg-2).
0 upgraded, 0 newly installed, 0 to remove and 22 not upgraded.
Reading package lists...
Building dependency tree...
Reading state information...
python3-rtree is already the newest version (0.8.3+ds-1).
0 upgraded, 0 newly installed, 0 to remove and 22 not upgraded.
time: 21 s


In [10]:
!pip install tqdm==4.36.0

time: 2.33 s


In [11]:
%load_ext autotime
import pandas as pd

import geopandas as gpd
import geopy
from geopy.geocoders import Nominatim
from geopy.extra.rate_limiter import RateLimiter

import matplotlib.pyplot as plt
import plotly_express as px
import tqdm
from tqdm import tqdm
from tqdm._tqdm_notebook import tqdm_notebook

import numpy as np

The autotime extension is already loaded. To reload it, use:
  %reload_ext autotime
time: 7.25 ms


In [12]:
from google.colab import files

uploaded = files.upload()
for fn in uploaded.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn, length=len(uploaded[fn])))
  

Saving All.plt to All (1).plt
User uploaded file "All.plt" with length 488569 bytes
time: 58.2 s


In [13]:
import io
df = pd.read_csv(io.BytesIO(uploaded[fn]))
df.columns = ['lat','lgt','allzero','alt','timestamp','date','time']
df.head()
df.shape

(7613, 7)

time: 29.3 ms


In [14]:
''' For Testing '''
import plotly.graph_objects as go
import pandas as pd
from plotly.validators.scatter.marker import SymbolValidator
from shapely.geometry import Point, Polygon

fig = go.Figure()
mapbox_access_token ="pk.eyJ1Ijoic2hha2Fzb20iLCJhIjoiY2plMWg1NGFpMXZ5NjJxbjhlM2ttN3AwbiJ9.RtGYHmreKiyBfHuElgYq_w"
raw_symbols = SymbolValidator().values
symbols = []
fig.add_trace(go.Scattermapbox(
        lat=df['lat'],
        lon=df['lgt'],
        mode='markers',
        marker=go.scattermapbox.Marker(
        size = 10,
        color='rgb(172, 173, 242)'
        ),
        text=df['date'],
    ))

# for drawing grid calculating the square grid cell 

staringLongitudePointA = 116.275446
staringLongitudePointB = 116.275446



trajectoryList = {"00"}
count = 0

startingLongitudePointA = 116.275446
startingLongitudePointB = 116.275446

startingLatitudePointA = 40.018702
startingLatitudePointB = 40.019702

longitudeCoordinate = []
latitudeCoordinate  = []

polygondata = []

for i in range(1,200):
    startingLongitudePointA = 116.275446
    startingLongitudePointB = 116.275446

    left = startingLongitudePointA

    startingLatitudePointA  =  startingLatitudePointA - .0010
    startingLatitudePointB  =  startingLatitudePointB - .0010

    for j in range(1,200):

        startingLongitudePointB = startingLongitudePointB + .0010
        
        polygondata.append([left,startingLatitudePointA,startingLongitudePointB,startingLatitudePointB])

        left = startingLongitudePointB


        longitudeCoordinate.append(startingLongitudePointA)       
        longitudeCoordinate.append(startingLongitudePointA)
        longitudeCoordinate.append(startingLongitudePointB)
        longitudeCoordinate.append(startingLongitudePointB)
        longitudeCoordinate.append(startingLongitudePointA)
        longitudeCoordinate.append(None)

        latitudeCoordinate.append(startingLatitudePointA)
        latitudeCoordinate.append(startingLatitudePointB)
        latitudeCoordinate.append(startingLatitudePointB)
        latitudeCoordinate.append(startingLatitudePointA)
        latitudeCoordinate.append(startingLatitudePointA)
        latitudeCoordinate.append(None)

        #coords = [(startingLongitudePointA, startingLatitudePointA), (startingLongitudePointA, startingLatitudePointB), (startingLongitudePointB, startingLatitudePointB), (startingLongitudePointB, startingLatitudePointA)]
        #polygon = Polygon(coords)
        
        """
        ifexist = toFindGridCell(startingLongitudePointA,startingLatitudePointA,startingLongitudePointA,startingLatitudePointB,startingLongitudePointB,startingLatitudePointB,startingLongitudePointB,startingLatitudePointA)
        if ifexist == True:
            count = count + 1
            st = ""
            st = str(i)+str(j)
            trajectoryList.add(st)
            #print(trajectoryList)
        """   

        

longitudeCoordinate.pop()
latitudeCoordinate.pop()

fig.add_trace(
    go.Scattermapbox(
    mode = "lines", fill = "none",
    lon = longitudeCoordinate,
    lat = latitudeCoordinate)
    )

fig.update_layout(
    autosize=True,
    hovermode='closest',
    mapbox=dict(
        accesstoken=mapbox_access_token,
        bearing=0,
        center=dict(
            lat=df['lat'][0],
            lon=df['lgt'][0]
        ),
        pitch=0,
        zoom=13,
        style='light'
    ),
)
print('TrajectoryList ', trajectoryList)
fig.show()

TrajectoryList  {'00'}


time: 5.17 s


In [15]:
from shapely.geometry import Point, Polygon
from geopandas.tools import sjoin
from shapely.geometry import box


dfPolygon = pd.DataFrame(polygondata, columns = ['left', 'bottom','right','top'])

geometry = [box(x1, y1, x2, y2) for x1,y1,x2,y2 in zip(dfPolygon.left, dfPolygon.bottom, dfPolygon.right, dfPolygon.top)]

geopolygon = gpd.GeoDataFrame(dfPolygon, geometry=geometry)

geopolygon.head()

point = [Point(xy) for xy in zip(df['lgt'], df['lat'])]

geopoint = gpd.GeoDataFrame(df, geometry=point)


points_polys = gpd.sjoin(geopoint, geopolygon, how="left")

listGeometry = points_polys['geometry']

listPointIndex = points_polys['index_right']

listPointIndex.sort_values()



freq = {}
for item in listPointIndex:
    if(item in freq):
        freq[item] += 1
    else: 
        freq[item] = 1
  



for key, value in freq.items():
    print("% d : % d"%(key, value))    


print(listPointIndex)

points_polys.head(20)

#print(len(points_polys))

#crs = {'init': 'epsg:4326'}

#gpd_df = gpd.GeoDataFrame(df, geometry = point)

#gpd_df.head()

0       6809
1       6808
2       6808
3       6808
4       6808
        ... 
7608    2432
7609    2432
7610    2431
7611    2431
7612    2431
Name: index_right, Length: 7613, dtype: int64


lat         lgt  allzero  ...     bottom       right        top
0   39.984683  116.318450        0  ...  39.983702  116.319446  39.984702
1   39.984686  116.318417        0  ...  39.983702  116.318446  39.984702
2   39.984688  116.318385        0  ...  39.983702  116.318446  39.984702
3   39.984655  116.318263        0  ...  39.983702  116.318446  39.984702
4   39.984611  116.318026        0  ...  39.983702  116.318446  39.984702
5   39.984608  116.317761        0  ...  39.983702  116.318446  39.984702
6   39.984563  116.317517        0  ...  39.983702  116.318446  39.984702
7   39.984539  116.317294        0  ...  39.983702  116.317446  39.984702
8   39.984606  116.317065        0  ...  39.983702  116.317446  39.984702
9   39.984568  116.316911        0  ...  39.983702  116.317446  39.984702
10  39.984586  116.316716        0  ...  39.983702  116.317446  39.984702
11  39.984561  116.316527        0  ...  39.983702  116.317446  39.984702
12  39.984536  116.316354        0  ...  39.983702  116.316446  39.984702
13  39.984523  116.316188        0  ...  39.983702  116.316446  39.984702
14  39.984516  116.315963        0  ...  39.983702  116.316446  39.984702
15  39.984523  116.315823        0  ...  39.983702  116.316446  39.984702
16  39.984574  116.315611        0  ...  39.983702  116.316446  39.984702
17  39.984568  116.315407        0  ...  39.983702  116.315446  39.984702
18  39.984538  116.315148        0  ...  39.983702  116.315446  39.984702
19  39.984501  116.314907        0  ...  39.983702  116.315446  39.984702

[20 rows x 13 columns]

time: 3.54 s


In [16]:

"""
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon


def toFindGridCell(pointA, pointB, pointC, pointD, pointE, pointF, pointG, pointH):
  print(pointA,' ',pointB,' ',pointC,' ',pointD,' ',pointE,' ',pointF,' ',pointG,' ',pointH)
  lons_vector = np.array([pointA,pointC,pointE,pointG])
  lats_vector = np.array([pointB,pointD,pointF,pointH])

  lons_lats_vect = np.column_stack((lons_vector, lats_vector)) # Reshape coordinates
  polygon = Polygon(lons_lats_vect) # create polygon

  for i in range(len(df)):
      point = Point(df['lat'][i],df['lgt'][i]) # create point
      #print(point)
      #print(polygon.contains(point)) # check if polygon contains point
      #print(point.within(polygon)) # check if a point is in the polygon 
  
   """ 


"\nfrom shapely.geometry import Point\nfrom shapely.geometry.polygon import Polygon\n\n\ndef toFindGridCell(pointA, pointB, pointC, pointD, pointE, pointF, pointG, pointH):\n  print(pointA,' ',pointB,' ',pointC,' ',pointD,' ',pointE,' ',pointF,' ',pointG,' ',pointH)\n  lons_vector = np.array([pointA,pointC,pointE,pointG])\n  lats_vector = np.array([pointB,pointD,pointF,pointH])\n\n  lons_lats_vect = np.column_stack((lons_vector, lats_vector)) # Reshape coordinates\n  polygon = Polygon(lons_lats_vect) # create polygon\n\n  for i in range(len(df)):\n      point = Point(df['lat'][i],df['lgt'][i]) # create point\n      #print(point)\n      #print(polygon.contains(point)) # check if polygon contains point\n      #print(point.within(polygon)) # check if a point is in the polygon \n  \n   "

time: 6.26 ms


In [17]:
from shapely.geometry import Point

from shapely.geometry.polygon import Polygon

from geopandas.tools import sjoin

def toFindGridCell(pointA, pointB, pointC, pointD, pointE, pointF, pointG, pointH):
  coords = [(pointB, pointA), (pointD, pointC), (pointF, pointE), (pointH, pointG)]
  polygon = Polygon(coords) # create polygon

  #point = [Point(xy) for xy in zip(df['lgt'], df['lat'])]
  
  #points_polys = gpd.sjoin(points, polys, how="left")
  #points_polys.head()

  for i in range(len(df)-1):
      point = Point(df['lat'][i],df['lgt'][i]) # create point
      if polygon.contains(point) == True:
        return True
        #print(polygon.contains(point))
        #print(point)
      elif point.within(polygon) == True:
        return True
        #print(point.within(polygon))
        #print(point)


time: 12.1 ms


In [18]:
from shapely.geometry import Point, Polygon

# Create Point objects
p1 = Point(40.007703, 116.275846)
p2 = Point(24.950999, 60.169159)

# Create a Polygon
coords = [(40.007702, 116.275446), (40.008702, 116.275446), (40.008702, 116.276446), (40.007702, 116.276446)]
poly = Polygon(coords)
# Let's check what we have
#print(p1)

#print(p2)


#print(poly)

# Check if p1 is within the polygon using the within function
if p1.within(poly) == True: 
  print(p1.within(poly))
elif polygon.contains(point):
  print(p2.within(poly))

# Check if p2 is within the polygon
p2.within(poly)



True


False

time: 16.1 ms


In [42]:
def trajectoryConstruction():    
    df = listPointIndex
    trajs_set = {}
    final_trajs = []
    for i in range(1):        
        for k in range(1):
            trajs = []
            for j in range(len(df)-1):                
                trajs.append(['h'+str(i),listPointIndex[j],listPointIndex[j+1]])                                    
            final_trajs.append(trajs)
        print('final_trajs ', final_trajs)
        trajs_set['h'+str(i)]=final_trajs
        print(trajs_set)        
    return trajs_set


time: 7.8 ms


In [36]:
def trajs_2_states(trajs):
    state_set_plates = {}
    action_set_plates = {}
    for plate in trajs:
        #print('Plate ',plate)
        state_set=set()
        action_set=set()
        for traj in trajs[plate]:
            #print('Traj ',traj)
            for i in range(len(traj)-1):
                state='|'.join(map(str,traj[i][1:]))
                #print('State ',state)
                action='|'.join(map(str,traj[i+1][1:3]))
                #print('action ',action)
                result='|'.join(map(str,traj[i+1][1:]))
                #print('result ',result)
                state_set.add(state)
                action_set.add(action)
                state_set.add(result)
        state_set_plates[plate] = state_set
        action_set_plates[plate] = action_set


    states_plates = {}
    actions_plates = {}
    for plate in state_set_plates:
        states=list(state_set_plates[plate])
        actions=list(action_set_plates[plate])
        states_plates[plate] = states
        actions_plates[plate] = actions

    state_index={}
    action_index={}
    for plate in states_plates:
        state_index[plate] = {}
        action_index[plate] = {}
        for i in range(len(states_plates[plate])):
            state_index[plate][states_plates[plate][i]]=i
        for i in range(len(actions_plates[plate])):
            action_index[plate][actions_plates[plate][i]]=i

    state_action_plates={}
    for plate in trajs:
        state_action_plates[plate] = {}
        for traj in trajs[plate]:
            for i in range(len(traj)-1):
                state='|'.join(map(str,traj[i][1:]))
                action='|'.join(map(str,traj[i+1][1:3]))
                s_i=state_index[plate][state]
                a_i=action_index[plate][action]
                if s_i not in state_action_plates[plate]:
                    state_action_plates[plate][s_i]=[a_i]
                elif a_i not in state_action_plates[plate][s_i]:
                    state_action_plates[plate][s_i].append(a_i)
    return states_plates, actions_plates, state_action_plates

time: 38.3 ms


In [43]:
trajectories = trajectoryConstruction()

states, actions, state_action = trajs_2_states(trajectories)

print('States', states)

print('actinons ', actions)

print('state_action ', state_action)


final_trajs  [[['h0', 6809, 6808], ['h0', 6808, 6808], ['h0', 6808, 6808], ['h0', 6808, 6808], ['h0', 6808, 6808], ['h0', 6808, 6808], ['h0', 6808, 6807], ['h0', 6807, 6807], ['h0', 6807, 6807], ['h0', 6807, 6807], ['h0', 6807, 6807], ['h0', 6807, 6806], ['h0', 6806, 6806], ['h0', 6806, 6806], ['h0', 6806, 6806], ['h0', 6806, 6806], ['h0', 6806, 6805], ['h0', 6805, 6805], ['h0', 6805, 6805], ['h0', 6805, 6805], ['h0', 6805, 6805], ['h0', 6805, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6804], ['h0', 6804, 6604], ['h0', 6604, 6604], ['h0', 6604, 6803], ['h0', 6803, 6803], ['h0', 6803, 6803], ['h0', 6803, 6802], ['h0', 6802, 6802], ['h0', 6802, 6802], ['h0', 6802, 6802], ['h0', 6802, 6802], ['h0', 6802, 6801], ['h0', 6801, 6801], ['h0', 6801, 6801], ['h0', 6801, 6801], ['h0', 6801, 6801], ['h0', 6801, 6801], ['h0', 6801, 6800], ['h0', 6800, 6800], ['h0'